In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly
from scipy import stats
from IPython.display import clear_output

In [2]:
%%time
total_rows = sum(1 for row in open('./microdados_enem_2019/DADOS/MICRODADOS_ENEM_2019.csv', 'r',encoding="ISO-8859-1"))
print(total_rows)

5095271
CPU times: user 6.6 s, sys: 3.57 s, total: 10.2 s
Wall time: 33.9 s


In [3]:
%%time
partial_read = True
partial_read_state = "RN"
partial_read_chunksize = 10000

data_full = pd.DataFrame()

if partial_read:
    for i,chunk in enumerate(pd.read_csv("./microdados_enem_2019/DADOS/MICRODADOS_ENEM_2019.csv", sep=';',encoding ="ISO-8859-1",chunksize=partial_read_chunksize),start=1):
        data_full = data_full.append(chunk.loc[chunk.SG_UF_PROVA=="RN"])
        ## SHOW % OF THE DATASET READED
        clear_output(wait=True)
        print(str(round(((i*partial_read_chunksize)/total_rows)*100,2))+"%")
else:
    #data = pd.read_csv("./microdados_enem_2019/DADOS/MICRODADOS_ENEM_2019.csv", sep=';',encoding ="ISO-8859-1",nrows=100000)
    pass

clear_output(wait=True)
print("read: 100%")

data_full

read: 100%
CPU times: user 2min 57s, sys: 16.5 s, total: 3min 13s
Wall time: 3min 13s


NU_INSCRICAO  NU_ANO  CO_MUNICIPIO_RESIDENCIA  \
134172   190001138801    2019                  2306900   
138161   190001142790    2019                  2306801   
138595   190001143224    2019                  2402501   
160067   190001164700    2019                  2304400   
165783   190001170416    2019                  2306207   
...               ...     ...                      ...   
5090724  190006114178    2019                  2411700   
5090725  190006114179    2019                  2402006   
5090726  190006114180    2019                  2401503   
5090727  190006114181    2019                  2406601   
5090728  190006114182    2019                  2408102   

        NO_MUNICIPIO_RESIDENCIA  CO_UF_RESIDENCIA SG_UF_RESIDENCIA  NU_IDADE  \
134172                Jaguaribe                23               CE        20   
138161              Jaguaribara                23               CE        25   
138595               Carnaubais                24               RN        18   
160067                Fortaleza                23               CE        18   
165783                 Itaiçaba                23               CE        17   
...                         ...               ...              ...       ...   
5090724     São Bento do Trairí                24               RN        19   
5090725                   Caicó                24               RN        21   
5090726               Barcelona                24               RN        24   
5090727           Lagoa Salgada                24               RN        47   
5090728                   Natal                24               RN        17   

        TP_SEXO  TP_ESTADO_CIVIL  TP_COR_RACA  ...  Q016  Q017 Q018  Q019  \
134172        F                1            3  ...     A     A    A     B   
138161        M                1            3  ...     A     A    A     B   
138595        M                1            1  ...     B     A    A     B   
160067        F                1            3  ...     B     A    B     B   
165783        F                1            3  ...     A     A    A     B   
...         ...              ...          ...  ...   ...   ...  ...   ...   
5090724       M                0            1  ...     A     A    A     B   
5090725       M                0            1  ...     A     A    A     B   
5090726       F                1            1  ...     A     A    A     C   
5090727       M                2            3  ...     B     A    A     C   
5090728       M                1            0  ...     B     A    B     E   

        Q020  Q021  Q022  Q023  Q024  Q025  
134172     A     A     B     A     A     B  
138161     A     A     B     A     A     A  
138595     A     A     C     A     B     B  
160067     B     A     D     A     B     B  
165783     A     A     C     A     A     B  
...      ...   ...   ...   ...   ...   ...  
5090724    A     A     C     A     A     A  
5090725    A     A     B     A     A     A  
5090726    B     A     D     A     A     A  
5090727    B     A     C     A     B     B  
5090728    B     B     E     A     D     B  

[119319 rows x 136 columns]

# Data cleanning and transforming

In [94]:
# TP_PRESENCA_X is 1 for present, 0 for miss and 2 for eliminated
data = data_full.loc[(data_full.TP_PRESENCA_CN==1)&(data_full.TP_PRESENCA_CH==1)&(data_full.TP_PRESENCA_LC==1)&(data_full.TP_PRESENCA_MT==1)].copy()
data['NU_NOTA_TOTAL'] = (data.NU_NOTA_CH+data.NU_NOTA_MT+data.NU_NOTA_LC+data.NU_NOTA_CN+data.NU_NOTA_REDACAO)/5
data

NU_INSCRICAO  NU_ANO  CO_MUNICIPIO_RESIDENCIA  \
138595   190001143224    2019                  2402501   
160067   190001164700    2019                  2304400   
165783   190001170416    2019                  2306207   
349973   190001354609    2019                  2408102   
448529   190001453166    2019                  2408102   
...               ...     ...                      ...   
5090724  190006114178    2019                  2411700   
5090725  190006114179    2019                  2402006   
5090726  190006114180    2019                  2401503   
5090727  190006114181    2019                  2406601   
5090728  190006114182    2019                  2408102   

        NO_MUNICIPIO_RESIDENCIA  CO_UF_RESIDENCIA SG_UF_RESIDENCIA  NU_IDADE  \
138595               Carnaubais                24               RN        18   
160067                Fortaleza                23               CE        18   
165783                 Itaiçaba                23               CE        17   
349973                    Natal                24               RN        29   
448529                    Natal                24               RN        17   
...                         ...               ...              ...       ...   
5090724     São Bento do Trairí                24               RN        19   
5090725                   Caicó                24               RN        21   
5090726               Barcelona                24               RN        24   
5090727           Lagoa Salgada                24               RN        47   
5090728                   Natal                24               RN        17   

        TP_SEXO  TP_ESTADO_CIVIL  TP_COR_RACA  ...  Q017  Q018 Q019  Q020  \
138595        M                1            1  ...     A     A    B     A   
160067        F                1            3  ...     A     B    B     B   
165783        F                1            3  ...     A     A    B     A   
349973        F                1            3  ...     A     A    B     B   
448529        M                0            3  ...     B     B    E     B   
...         ...              ...          ...  ...   ...   ...  ...   ...   
5090724       M                0            1  ...     A     A    B     A   
5090725       M                0            1  ...     A     A    B     A   
5090726       F                1            1  ...     A     A    C     B   
5090727       M                2            3  ...     A     A    C     B   
5090728       M                1            0  ...     A     B    E     B   

        Q021  Q022  Q023  Q024  Q025  NU_NOTA_TOTAL  
138595     A     C     A     B     B         498.62  
160067     A     D     A     B     B         690.72  
165783     A     C     A     A     B         587.70  
349973     A     D     A     B     B         414.70  
448529     B     E     B     E     B         662.88  
...      ...   ...   ...   ...   ...            ...  
5090724    A     C     A     A     A         530.16  
5090725    A     B     A     A     A         460.00  
5090726    A     D     A     A     A         498.50  
5090727    A     C     A     B     B         453.14  
5090728    B     E     A     D     B         536.38  

[90557 rows x 137 columns]

In [95]:
questions = {}

questions["Q024"]={"text":"quantidade de computadores","A":"Nenhum","B":"Um","C":"Dois","D":"Três","E":"Quatro ou mais"}
questions["Q025"]={"text":"possuir ou não serviço de internet","A":"Não","B":"Sim"}

columns = list(questions.keys())+["NU_NOTA_TOTAL"]

data = data.loc[:,columns].reset_index(drop=True).rename(columns={"NU_NOTA_TOTAL":"Notas"})
data

Q024 Q025   Notas
0        B    B  498.62
1        B    B  690.72
2        A    B  587.70
3        B    B  414.70
4        E    B  662.88
...    ...  ...     ...
90552    A    A  530.16
90553    A    A  460.00
90554    A    A  498.50
90555    B    B  453.14
90556    D    B  536.38

[90557 rows x 3 columns]

# Data visualization

In [96]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90557 entries, 0 to 90556
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Q024    90557 non-null  object 
 1   Q025    90557 non-null  object 
 2   Notas   90557 non-null  float64
dtypes: float64(1), object(2)
memory usage: 2.1+ MB


In [106]:
def putValue(value,dict_):
    return dict_[str(value)]

#QUANTIDADE DE NOTAS POR INDICADOR SOCIOECONOMICO
for key in questions.keys():
    count = data[key].value_counts()
    count.index = count.index.map(questions[key])
    print("Notas por "+str(questions[key]['text'])+" :")
    display(count)
    grades = data.groupby(by=key).mean()
    grades.index = grades.index.map(questions[key])
    fig = px.line(grades,width=400, height=400)
    fig.update_layout(xaxis_title=questions[key]['text'],yaxis_title="notas")
    fig.show()

Notas por quantidade de computadores :


Nenhum            43894
Um                38296
Dois               5992
Três               1687
Quatro ou mais      688
Name: Q024, dtype: int64

Notas por possuir ou não serviço de internet :


Sim    71732
Não    18825
Name: Q025, dtype: int64

In [121]:
def remove_outliers(data_,column):
    z_scores = stats.zscore(data_[column])
    abs_z_scores = np.abs(z_scores)
    filtered_entries = (abs_z_scores < 2.5)
    return data_[filtered_entries]

def getGradesPerValues(data,question_key,answers):
    grades = []
    for answer_key in answers.keys():
        if answer_key!="text":
            grade = remove_outliers(data.loc[data[question_key]==answer_key],"Notas")
            grade[question_key] = answers[answer_key]
            grades.append(grade)
    return grades

def addDispersion(fig,grade,name):
    fig.add_trace(
        plotly.graph_objects.Violin(y=grade["Notas"],name=name,box_visible=True,meanline_visible=True)
    )

for question_key in questions.keys():
    fig = plotly.graph_objects.Figure()
    grades = getGradesPerValues(data,question_key,questions[question_key])
    for grade in grades:
        addDispersion(fig,grade,grade[question_key].values[0])
    fig.update_layout(title="Correlação entre notas e "+str(questions[question_key]['text']+" (Enem 2019)."),
                      xaxis_title=str(questions[question_key]['text']),
                      yaxis_title="notas dos participantes",
                      title_x=0.5,template="plotly_dark")
    fig.show()